## ДЗ 3. Word2vec & Fasttext   Еще не сделано

In [ ]:
Используем предобработанные в рамках 1-ого домашнего задания датасет. Используем столбец 'clean_tweet'.

In [2]:
import re
import numpy as np
import pandas as pd
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel
import matplotlib.pyplot as plt
%matplotlib inline
from nltk.corpus import stopwords

stop_words = stopwords.words('english')
stop_words.extend(['from', 'subject', 're', 'edu', 'use'])
import pickle

In [16]:
import requests
from bs4 import BeautifulSoup
import re

def url_to_string(url):
    res = requests.get(url)
    html = res.text
    soup = BeautifulSoup(html, 'html5lib')
    for script in soup(["script", "style", 'aside']):
        script.extract()
    return " ".join(re.split(r'[\n\t]+', soup.get_text()))

In [21]:
combine_df = pd.read_pickle("./words.pkl")
combine_df .head()

id  label                                              tweet  \
0   1    0.0   @user when a father is dysfunctional and is s...   
1   2    0.0  @user @user thanks for #lyft credit i can't us...   
2   3    0.0                                bihday your majesty   
3   4    0.0  #model   i love u take with u all the time in ...   
4   5    0.0             factsguide: society now    #motivation   

                                         clean_tweet  \
0  when father is dysfunctional and is so selfish...   
1  thanks for lyft credit cannot use cause they d...   
2                                bihday your majesty   
3    model love you take with you all the time in ur   
4                  factsguide society now motivation   

                                         tweet_token  \
0  [when, father, is, dysfunctional, and, is, so,...   
1  [thanks, for, lyft, credit, can, not, use, cau...   
2                            [bihday, your, majesty]   
3  [model, love, you, take, with, you, all, the, ...   
4             [factsguide, society, now, motivation]   

                                tweet_token_filtered  \
0  [father, dysfunctional, selfish, drags, kids, ...   
1  [thanks, lyft, credit, use, cause, offer, whee...   
2                                  [bihday, majesty]   
3                      [model, love, take, time, ur]   
4                  [factsguide, society, motivation]   

                                       tweet_stemmed  \
0  [father, dysfunct, selfish, drag, kid, dysfunc...   
1  [thank, lyft, credit, use, caus, offer, wheelc...   
2                                  [bihday, majesti]   
3                      [model, love, take, time, ur]   
4                        [factsguid, societi, motiv]   

                                    tweet_lemmatized  
0  [father, dysfunctional, selfish, drag, kid, dy...  
1  [thanks, lyft, credit, use, cause, offer, whee...  
2                                  [bihday, majesty]  
3                      [model, love, take, time, ur]  
4                  [factsguide, society, motivation]

In [23]:
df_clean_tweet = combine_df ['clean_tweet'] 
clean_tweet = df_clean_tweet.to_numpy()
clean_tweet

array(['when father is dysfunctional and is so selfish he drags his kids into his dysfunction run',
       'thanks for lyft credit cannot use cause they do not offer wheelchair vans in pdx disapointed getthanked',
       'bihday your majesty', ...,
       'hillary campaigned today in ohio omg used words like assets liability never once did clinton say thee word radicalization',
       'happy at work conference right mindset leads to culture of development organizations work mindset',
       'my song so glad free download shoegaze newmusic newsong'],
      dtype=object)

Задание 1.
Используя библиотеку Spacy, вывести ТОП-20 популярных NER в combine_df датасете. Какой тип NER (ORG, GPE, PERSON и тд) оказался самым популярным? (Учтите, что max_word_limit_spacy для Spacy = 1000000)
С помощью Spacy выяснить: какие персоны и организации самые обсуждаемые в train и test датасетах? вывести ТОП-20 самых популярных. Действительно ли в топ вошли только персоны и организации или есть мусор?
Повторим шаги из заданий 1 и 2, используя библиотеку nltk.



In [29]:
import spacy
from spacy import displacy
import en_core_web_md

nlp = en_core_web_md.load()


In [27]:
text = ''
for i in range(combine_df.shape[0]):
    text += combine_df['clean_tweet'][i]
    if len(text)> 900000:
        break


In [28]:
nlp_text = nlp(text)
displacy.render(nlp_text, jupyter=True, style='ent')

Задание 2.
Используя библиотеку nltk, вывести ТОП-20 популярных NER в combine_df датасете. Какой тип NER (ORG, GPE, PERSON и тд) оказался самым популярным? Для данного задания используем ограничение на количество символов во входном датасете (max_word_limit_spacy = 1000000), чтобы иметь возможность сравнить результаты работы Spacy и nltk. Обратите внимание, что nltk чувствителен к регистру.
С помощью nltk выяснить: какие персоны и организации самые обсуждаемые в train и test датасетах? вывести ТОП-20 самых популярных. Действительно ли в топ вошли только персоны и организации или есть мусор?


In [6]:
import nltk
from nltk.tag import SequentialBackoffTagger
from nltk.corpus import names
#nltk.download('names')
#nltk.download('averaged_perceptron_tagger')

In [7]:
class NamesTagger(SequentialBackoffTagger):
    def __init__(self, *args, **kwargs):
        SequentialBackoffTagger.__init__(self, *args, **kwargs)
        self.name_set = set([n.lower() for n in names.words()])
            
    def choose_tag(self, tokens, index, history):
        word = tokens[index]
        if word.lower() in self.name_set:
             return 'NNP'
        else:
             return None
            
nt = NamesTagger()
print(nt.tag(['Katya'])) 
print(nt.tag(['Adam'])) 
print(nt.tag(['Window']))

[('Katya', 'NNP')]
[('Adam', 'NNP')]
[('Window', None)]


In [11]:
nltk.pos_tag(['when father is dysfunctional and is so selfish'])

[('when father is dysfunctional and is so selfish', 'NN')]

Задание 3.
Какая из библиотек по вашему лучше отработала? Сравните качество полученных most_common NER и количество распознаных NER.
